In [2]:
import MetaTrader5 as mt5 #mt5 to access historcal data
import pandas as pd # for data analysis and calculation of technical indcator
import numpy as np
import plotly.io as pio
import plotly.express as px # for data visualization
import plotly.graph_objects as go
import tdclient as TDClient
from datetime import datetime, time ,timezone #to specify the date time range for historical data
from IPython.display import display, Markdown, Latex # to display result in python notebook
from backtest import Backtester, get_ohlc_history, create_price_fig, evaluate_backtest

In [3]:
# Conecte mt5
mt5.initialize()
# logine mt5
login = 52185665
password = '3cAJz$AQiKwMq0'
server = 'ICMarketsSC-Demo'

mt5.login(login,password,server)

True

In [4]:
# this function retreives olhc data from mt5 account and return a data frame
def get_ohlc(symbol, timeframe, start_datetime, end_datetime):
    ohlc = mt5.copy_rates_range(symbol, timeframe, start_datetime, end_datetime)
    ohlc_df = pd.DataFrame(ohlc)
    ohlc_df['time'] = pd.to_datetime(ohlc_df['time'], unit= 's')
    return ohlc_df[['time', 'open', 'high', 'low', 'close']]


In [5]:
# 1 minut df
symbol = 'EURUSD'
pos_size = 1
timeframe = mt5.TIMEFRAME_M5
start_datetime = datetime(2024,12,15)
end_datetime = datetime.now()
ohlc_df = get_ohlc(symbol, timeframe, start_datetime, end_datetime)
ohlc_df

time     open     high      low    close
0     2024-12-16 00:00:00  1.04850  1.04863  1.04797  1.04856
1     2024-12-16 00:05:00  1.04856  1.04865  1.04854  1.04856
2     2024-12-16 00:10:00  1.04856  1.04871  1.04853  1.04862
3     2024-12-16 00:15:00  1.04862  1.04880  1.04857  1.04867
4     2024-12-16 00:20:00  1.04871  1.04876  1.04857  1.04864
...                   ...      ...      ...      ...      ...
50653 2025-08-20 21:05:00  1.16611  1.16636  1.16589  1.16636
50654 2025-08-20 21:10:00  1.16636  1.16661  1.16624  1.16627
50655 2025-08-20 21:15:00  1.16627  1.16633  1.16581  1.16591
50656 2025-08-20 21:20:00  1.16591  1.16593  1.16565  1.16567
50657 2025-08-20 21:25:00  1.16567  1.16596  1.16553  1.16580

[50658 rows x 5 columns]

In [6]:
# hour4 df
timeframe = mt5.TIMEFRAME_H4
hourly_df = get_ohlc(symbol, timeframe, start_datetime, end_datetime)
hourly_df.tail(5)

time     open     high      low    close
1051 2025-08-20 04:00:00  1.16388  1.16423  1.16222  1.16344
1052 2025-08-20 08:00:00  1.16345  1.16467  1.16232  1.16379
1053 2025-08-20 12:00:00  1.16379  1.16737  1.16349  1.16710
1054 2025-08-20 16:00:00  1.16710  1.16719  1.16463  1.16598
1055 2025-08-20 20:00:00  1.16598  1.16725  1.16469  1.16502

In [7]:
# daily df
timeframe = mt5.TIMEFRAME_D1
daily_df = get_ohlc(symbol, timeframe, start_datetime, end_datetime)
daily_df

time     open     high      low    close
0   2024-12-16  1.04850  1.05248  1.04746  1.05114
1   2024-12-17  1.05105  1.05343  1.04793  1.04915
2   2024-12-18  1.04907  1.05128  1.03437  1.03495
3   2024-12-19  1.03514  1.04224  1.03440  1.03629
4   2024-12-20  1.03650  1.04475  1.03431  1.04268
..         ...      ...      ...      ...      ...
171 2025-08-14  1.17051  1.17152  1.16310  1.16482
172 2025-08-15  1.16469  1.17153  1.16422  1.17025
173 2025-08-18  1.17065  1.17145  1.16560  1.16609
174 2025-08-19  1.16601  1.16929  1.16390  1.16465
175 2025-08-20  1.16443  1.16737  1.16222  1.16502

[176 rows x 5 columns]

In [8]:
# Calculate Pivot Point, R1, R2, R3, stopeR4, S1, S2, S3, stopeS4 levels with Fibonacci 
daily_df["pivot"] = ((daily_df["high"] + daily_df["low"] + daily_df["close"]) / 3).shift(1)
daily_df["prange"] = (daily_df["high"] - daily_df["low"]).shift(1)
daily_df["R1"] = daily_df["pivot"] + 0.382 * daily_df["prange"]
daily_df["R2"] = daily_df["pivot"] + 0.618 * daily_df["prange"]
daily_df["R3"] = daily_df["pivot"] + 1.000 * daily_df["prange"]

daily_df["S1"] = daily_df["pivot"] - 0.382 * daily_df["prange"]
daily_df["S2"] = daily_df["pivot"] - 0.618 * daily_df["prange"]
daily_df["S3"] = daily_df["pivot"] - 1.000 * daily_df["prange"]
daily_df[["time","S2","R2"]].tail(10)


time        S2        R2
166 2025-08-07  1.156236  1.169671
167 2025-08-08  1.160368  1.171232
168 2025-08-11  1.161817  1.168083
169 2025-08-12  1.157423  1.168003
170 2025-08-13  1.159521  1.171733
171 2025-08-14  1.166012  1.174008
172 2025-08-15  1.161276  1.171684
173 2025-08-18  1.164149  1.173184
174 2025-08-19  1.164098  1.171329
175 2025-08-20  1.162616  1.169278

In [9]:
#setting the sma 1 and 14 periods
furst_sma_period = 1
second_sma_period = 14
#ohlc4
hourly_df['ohlc4'] = (hourly_df['open'] + hourly_df['high'] + hourly_df['low'] + hourly_df['close']) / 4

# sma 1
hourly_df['sma_1'] = hourly_df['ohlc4'].rolling(furst_sma_period).mean()
hourly_df['prev_sma_1'] = hourly_df['sma_1'].shift(1) #to find crossovers, previous sma value is necessary using shift()
# sma 14
hourly_df['sma_14'] = hourly_df['ohlc4'].rolling(second_sma_period).mean()
hourly_df

time     open     high      low    close     ohlc4  \
0    2024-12-16 00:00:00  1.04850  1.05213  1.04797  1.05190  1.050125   
1    2024-12-16 04:00:00  1.05191  1.05230  1.05098  1.05196  1.051788   
2    2024-12-16 08:00:00  1.05196  1.05248  1.05003  1.05051  1.051245   
3    2024-12-16 12:00:00  1.05051  1.05084  1.04833  1.05078  1.050115   
4    2024-12-16 16:00:00  1.05075  1.05207  1.04746  1.05112  1.050350   
...                  ...      ...      ...      ...      ...       ...   
1051 2025-08-20 04:00:00  1.16388  1.16423  1.16222  1.16344  1.163442   
1052 2025-08-20 08:00:00  1.16345  1.16467  1.16232  1.16379  1.163558   
1053 2025-08-20 12:00:00  1.16379  1.16737  1.16349  1.16710  1.165437   
1054 2025-08-20 16:00:00  1.16710  1.16719  1.16463  1.16598  1.166225   
1055 2025-08-20 20:00:00  1.16598  1.16725  1.16469  1.16502  1.165735   

         sma_1  prev_sma_1    sma_14  
0     1.050125         NaN       NaN  
1     1.051788    1.050125       NaN  
2     1.051245    1.051788       NaN  
3     1.050115    1.051245       NaN  
4     1.050350    1.050115       NaN  
...        ...         ...       ...  
1051  1.163442    1.164090  1.166895  
1052  1.163558    1.163442  1.166394  
1053  1.165437    1.163558  1.166043  
1054  1.166225    1.165437  1.165826  
1055  1.165735    1.166225  1.165676  

[1056 rows x 9 columns]

In [10]:
#setting the 11 and 114 sma periods
thurd_sma_period = 1
fourth_sma_period = 14
#ohlc4
daily_df['ohlc4'] = (daily_df['open'] + daily_df['high'] + daily_df['low'] + daily_df['close']) / 4
# sma 11
daily_df['sma_11'] = daily_df['ohlc4'].rolling(thurd_sma_period).mean()
daily_df['prev_sma_11'] = daily_df['sma_11'].shift(1) #to find crossovers, previous sma value is necessary using shift()
# sma 114
daily_df['sma_114'] = daily_df['ohlc4'].rolling(fourth_sma_period).mean()
daily_df[["time","sma_11","sma_114","prev_sma_11"]]

time    sma_11   sma_114  prev_sma_11
0   2024-12-16  1.049895       NaN          NaN
1   2024-12-17  1.050390       NaN     1.049895
2   2024-12-18  1.042417       NaN     1.050390
3   2024-12-19  1.037017       NaN     1.042417
4   2024-12-20  1.039560       NaN     1.037017
..         ...       ...       ...          ...
171 2025-08-14  1.167488  1.159613     1.169358
172 2025-08-15  1.167673  1.159629     1.167488
173 2025-08-18  1.168448  1.160498     1.167673
174 2025-08-19  1.165963  1.161777     1.168448
175 2025-08-20  1.164760  1.163409     1.165963

[176 rows x 4 columns]

In [11]:
#setting entring and closing time and one trade a day
# Set the start and end times for your desired trading hours
start_time = datetime.strptime('06:00:00', '%H:%M:%S').time()
end_time = datetime.strptime('17:00:00', '%H:%M:%S').time()
end_trading_section = datetime.strptime('23:45:00', '%H:%M:%S').time()

# Filter the trade data for trades within the specified trading hours
#trades_within_hours = daily_df[(daily_df['time'].dt.time >= start_time) & (daily_df['time'].dt.time <= end_time)]
# open one trade a day
first_trade_per_day = daily_df.groupby(daily_df['time'].dt.time).first()
# Close all open positions at 11:45 PM
open_positions = daily_df[daily_df['time'].dt.time == end_trading_section]

# function to trading
daily_df["sell_stope_loss"] = (daily_df["R2"] - daily_df["S1"]) /2 + daily_df["R2"] 
daily_df["buy_stope_loss"] = (daily_df["S2"] - ((daily_df["R1"] - daily_df["S2"]) /2))
daily_df['sell_profit'] = daily_df['low'] <= daily_df["S1"]
daily_df['buy_profit'] = daily_df["high"] >= daily_df["R1"]
daily_df

time     open     high      low    close     pivot   prange  \
0   2024-12-16  1.04850  1.05248  1.04746  1.05114       NaN      NaN   
1   2024-12-17  1.05105  1.05343  1.04793  1.04915  1.050360  0.00502   
2   2024-12-18  1.04907  1.05128  1.03437  1.03495  1.050170  0.00550   
3   2024-12-19  1.03514  1.04224  1.03440  1.03629  1.040200  0.01691   
4   2024-12-20  1.03650  1.04475  1.03431  1.04268  1.037643  0.00784   
..         ...      ...      ...      ...      ...       ...      ...   
171 2025-08-14  1.17051  1.17152  1.16310  1.16482  1.170010  0.00647   
172 2025-08-15  1.16469  1.17153  1.16422  1.17025  1.166480  0.00842   
173 2025-08-18  1.17065  1.17145  1.16560  1.16609  1.168667  0.00731   
174 2025-08-19  1.16601  1.16929  1.16390  1.16465  1.167713  0.00585   
175 2025-08-20  1.16443  1.16737  1.16222  1.16502  1.165947  0.00539   

           R1        R2        R3  ...        S2        S3     ohlc4  \
0         NaN       NaN       NaN  ...       NaN       NaN  1.049895   
1    1.052278  1.053462  1.055380  ...  1.047258  1.045340  1.050390   
2    1.052271  1.053569  1.055670  ...  1.046771  1.044670  1.042417   
3    1.046660  1.050650  1.057110  ...  1.029750  1.023290  1.037017   
4    1.040638  1.042488  1.045483  ...  1.032798  1.029803  1.039560   
..        ...       ...       ...  ...       ...       ...       ...   
171  1.172482  1.174008  1.176480  ...  1.166012  1.163540  1.167488   
172  1.169696  1.171684  1.174900  ...  1.161276  1.158060  1.167673   
173  1.171459  1.173184  1.175977  ...  1.164149  1.161357  1.168448   
174  1.169948  1.171329  1.173563  ...  1.164098  1.161863  1.165963   
175  1.168006  1.169278  1.171337  ...  1.162616  1.160557  1.164760   

       sma_11  prev_sma_11   sma_114  sell_stope_loss  buy_stope_loss  \
0    1.049895          NaN       NaN              NaN             NaN   
1    1.050390     1.049895       NaN         1.055972        1.044748   
2    1.042417     1.050390       NaN         1.056319        1.044021   
3    1.037017     1.042417       NaN         1.059105        1.021295   
4    1.039560     1.037017       NaN         1.046408        1.028878   
..        ...          ...       ...              ...             ...   
171  1.167488     1.169358  1.159613         1.177243        1.162777   
172  1.167673     1.167488  1.159629         1.175894        1.157066   
173  1.168448     1.167673  1.160498         1.176839        1.160494   
174  1.165963     1.168448  1.161777         1.174254        1.161173   
175  1.164760     1.165963  1.163409         1.171973        1.159921   

     sell_profit  buy_profit  
0          False       False  
1           True        True  
2           True       False  
3          False       False  
4           True        True  
..           ...         ...  
171         True       False  
172        False        True  
173         True       False  
174         True       False  
175         True       False  

[176 rows x 21 columns]

In [12]:
def entring_stoploss_profit(row, ohlc_df) :
    hour = row['time'].hour
    week = row['time'].dayofweek
    if row["prev_sma_11"] > row['sma_114'] and row["low_x"] <= row["S2"]:# and (hour >= 10 and hour < 18):
        return "buy"
    elif row['prev_sma_11'] < row['sma_114'] and row["high_x"] >= row["R2"]:# and (hour >= 10 and hour < 18):
        return "sell"
    # Merge daily indicators into minute data (asof = merge on closest earlier date)
merged_df = pd.merge_asof(ohlc_df, daily_df, on='time', direction='backward')
merged_df["signal"] = merged_df.apply(entring_stoploss_profit, axis=1, ohlc_df = ohlc_df)

# Tag first signal per day in original merged_df
merged_df['is_first_signal'] = (merged_df[merged_df["signal"].notna()].groupby(merged_df["time"].dt.date).cumcount() == 0)

# Set signal only on the first row per day, others = None
merged_df['signal'] = merged_df.apply(lambda row: row['signal'] if row['is_first_signal'] else None, axis=1)
merged_df[['signal', 'time']].dropna()

signal                time
3858    sell 2025-01-06 09:30:00
5482    sell 2025-01-14 00:50:00
5946    sell 2025-01-15 15:30:00
6541    sell 2025-01-17 17:05:00
6810    sell 2025-01-20 15:30:00
...      ...                 ...
47940   sell 2025-08-07 11:00:00
48566    buy 2025-08-11 15:10:00
49434    buy 2025-08-14 15:30:00
50166    buy 2025-08-19 04:30:00
50460    buy 2025-08-20 05:00:00

[62 rows x 2 columns]

In [13]:
merged_df = merged_df.rename(columns={
    "low_x": "low",
    "high_x": "high",
    "open_x": "open",
    "close_x": "close",
    "low_y": "daily_low",
    "high_y": "daily_high",
    "open_y": "daily_open",
    "close_y": "daily_close"
})


In [14]:
print(merged_df.columns.tolist())
merged_df


['time', 'open', 'high', 'low', 'close', 'daily_open', 'daily_high', 'daily_low', 'daily_close', 'pivot', 'prange', 'R1', 'R2', 'R3', 'S1', 'S2', 'S3', 'ohlc4', 'sma_11', 'prev_sma_11', 'sma_114', 'sell_stope_loss', 'buy_stope_loss', 'sell_profit', 'buy_profit', 'signal', 'is_first_signal']


time     open     high      low    close  daily_open  \
0     2024-12-16 00:00:00  1.04850  1.04863  1.04797  1.04856     1.04850   
1     2024-12-16 00:05:00  1.04856  1.04865  1.04854  1.04856     1.04850   
2     2024-12-16 00:10:00  1.04856  1.04871  1.04853  1.04862     1.04850   
3     2024-12-16 00:15:00  1.04862  1.04880  1.04857  1.04867     1.04850   
4     2024-12-16 00:20:00  1.04871  1.04876  1.04857  1.04864     1.04850   
...                   ...      ...      ...      ...      ...         ...   
50653 2025-08-20 21:05:00  1.16611  1.16636  1.16589  1.16636     1.16443   
50654 2025-08-20 21:10:00  1.16636  1.16661  1.16624  1.16627     1.16443   
50655 2025-08-20 21:15:00  1.16627  1.16633  1.16581  1.16591     1.16443   
50656 2025-08-20 21:20:00  1.16591  1.16593  1.16565  1.16567     1.16443   
50657 2025-08-20 21:25:00  1.16567  1.16596  1.16553  1.16580     1.16443   

       daily_high  daily_low  daily_close     pivot  ...     ohlc4    sma_11  \
0         1.05248    1.04746      1.05114       NaN  ...  1.049895  1.049895   
1         1.05248    1.04746      1.05114       NaN  ...  1.049895  1.049895   
2         1.05248    1.04746      1.05114       NaN  ...  1.049895  1.049895   
3         1.05248    1.04746      1.05114       NaN  ...  1.049895  1.049895   
4         1.05248    1.04746      1.05114       NaN  ...  1.049895  1.049895   
...           ...        ...          ...       ...  ...       ...       ...   
50653     1.16737    1.16222      1.16502  1.165947  ...  1.164760  1.164760   
50654     1.16737    1.16222      1.16502  1.165947  ...  1.164760  1.164760   
50655     1.16737    1.16222      1.16502  1.165947  ...  1.164760  1.164760   
50656     1.16737    1.16222      1.16502  1.165947  ...  1.164760  1.164760   
50657     1.16737    1.16222      1.16502  1.165947  ...  1.164760  1.164760   

       prev_sma_11   sma_114  sell_stope_loss  buy_stope_loss  sell_profit  \
0              NaN       NaN              NaN             NaN        False   
1              NaN       NaN              NaN             NaN        False   
2              NaN       NaN              NaN             NaN        False   
3              NaN       NaN              NaN             NaN        False   
4              NaN       NaN              NaN             NaN        False   
...            ...       ...              ...             ...          ...   
50653     1.165963  1.163409         1.171973        1.159921         True   
50654     1.165963  1.163409         1.171973        1.159921         True   
50655     1.165963  1.163409         1.171973        1.159921         True   
50656     1.165963  1.163409         1.171973        1.159921         True   
50657     1.165963  1.163409         1.171973        1.159921         True   

       buy_profit  signal  is_first_signal  
0           False    None              NaN  
1           False    None              NaN  
2           False    None              NaN  
3           False    None              NaN  
4           False    None              NaN  
...           ...     ...              ...  
50653       False    None              NaN  
50654       False    None              NaN  
50655       False    None              NaN  
50656       False    None              NaN  
50657       False    None              NaN  

[50658 rows x 27 columns]

In [15]:
# create trade logic
def on_bar(data, trades, orders):
    open_trades = trades[trades['state'] == 'open']
    num_open_trades = open_trades.shape[0]
    if 'signal' not in data:
        print("Warning: 'signal' column is missing!")
        return
    account_balance = 10000  # your account in USD
    risk_percent = 0.20  # 2%
    pip_value_per_lot = 10  # on EURUSD, 1 lot = $10 per pip
    risk_amount = account_balance * risk_percent
    # entry signal
    if data['signal'] == 'buy' and not num_open_trades:
        stop_loss_pips = data['S2'] - (data["S2"] - ((data["R1"] - data["S2"]) /2)) # example SL
        volume = risk_amount / (stop_loss_pips * pip_value_per_lot)
        orders.open_trade(symbol, volume, 'buy')
    
    elif data['signal'] == 'sell' and not num_open_trades:
        stop_loss_pips = ((data["R2"] - data["S1"]) /2 + data["R2"]) - data["R2"]
        volume = risk_amount / (stop_loss_pips * pip_value_per_lot)
        orders.open_trade(symbol, volume, 'sell')
        
# exit signal
    if num_open_trades:
        trade = open_trades.iloc[0]

        if trade['order_type'] == 'buy' and ((data["low"] <= data["S2"] - ((data["R1"] - data["S2"]) /2))):
                                            #or (data["high"] >= data["R1"])
                                            #or (data['time'].time() == pd.to_datetime('23:00:00').time())):
            orders.close_trade(trade)
        elif trade['order_type'] == 'sell' and ((data["high"] >= (data["R2"] - data["S1"]) /2 + data["R2"])):
                                            #or (data["low"] <= data["S1"])
                                            #or (data['time'].time() == pd.to_datetime('23:00:00').time())):
            orders.close_trade(trade)

In [16]:
# backtest parameters
starting_balance = 10000
currency = 'USD'
exchange_rate = 1
commission = -7 / 100000

# backtest
bt = Backtester()
bt.set_starting_balance(starting_balance, currency=currency)
bt.set_exchange_rate(exchange_rate)
bt.set_commission(commission)

bt.set_historical_data(merged_df)
bt.set_on_bar(on_bar)

get_ohlc_history(symbol, timeframe, start_datetime, end_datetime)
bt.run_backtest()

bt.trades

state  symbol order_type         volume            open_time open_price  \
0   closed  EURUSD       sell   70175.438596  2025-01-06 09:30:00    1.03191   
1   closed  EURUSD       sell   55096.418733  2025-01-14 00:50:00    1.02647   
2   closed  EURUSD       sell   56737.588652  2025-01-15 15:30:00    1.03007   
3   closed  EURUSD        buy   61633.281972  2025-01-23 18:10:00    1.03964   
4   closed  EURUSD       sell   28735.632184  2025-02-04 18:45:00    1.03823   
5   closed  EURUSD       sell   44792.833147  2025-02-12 19:00:00    1.03914   
6   closed  EURUSD        buy   74487.895717  2025-02-27 06:30:00    1.04657   
7   closed  EURUSD       sell   66666.666667  2025-03-03 03:10:00    1.04202   
8   closed  EURUSD       sell   34752.389227  2025-03-04 13:50:00    1.05266   
9   closed  EURUSD        buy   73529.411765  2025-03-13 10:35:00    1.08682   
10  closed  EURUSD        buy   64308.681672  2025-03-19 10:35:00    1.09024   
11  closed  EURUSD        buy   46783.625731  2025-03-20 12:20:00    1.08543   
12  closed  EURUSD        buy   77519.379845  2025-04-30 04:55:00    1.13684   
13  closed  EURUSD       sell   53191.489362  2025-05-02 12:35:00    1.13388   
14  closed  EURUSD        buy   48134.777377  2025-05-22 18:05:00    1.12812   
15  closed  EURUSD        buy   44198.895028  2025-06-06 15:30:00     1.1407   
16  closed  EURUSD        buy   58565.153734  2025-07-02 14:35:00    1.17575   
17  closed  EURUSD        buy  100502.512563  2025-07-10 16:50:00    1.16957   
18  closed  EURUSD       sell    40040.04004  2025-07-16 18:15:00    1.16203   
19  closed  EURUSD       sell   66555.740433  2025-08-06 13:10:00     1.1594   
20  closed  EURUSD       sell   36798.528059  2025-08-07 11:00:00    1.16895   

             close_time close_price sl tp info   profit commission  \
0   2025-01-06 11:00:00     1.03503  0  0   {}  -218.95  -4.912281   
1   2025-01-14 21:35:00     1.03025  0  0   {}  -208.26  -3.856749   
2   2025-01-20 15:30:00     1.03139  0  0   {}   -74.89  -3.971631   
3   2025-02-03 00:00:00     1.02357  0  0   {}  -990.45   -4.31433   
4   2025-02-11 21:40:00     1.03623  0  0   {}    57.47  -2.011494   
5   2025-02-20 20:15:00     1.04949  0  0   {}  -463.61  -3.135498   
6   2025-02-27 15:50:00      1.0446  0  0   {}  -146.74  -5.214153   
7   2025-03-03 13:30:00     1.04504  0  0   {}  -201.33  -4.666667   
8   2025-03-04 20:55:00      1.0587  0  0   {}  -209.90  -2.432667   
9   2025-03-13 15:45:00      1.0839  0  0   {}  -214.71  -5.147059   
10  2025-03-19 20:35:00     1.08654  0  0   {}  -237.94  -4.501608   
11  2025-04-23 01:25:00     1.13409  0  0   {}  2276.49  -3.274854   
12  2025-04-30 18:25:00     1.13459  0  0   {}  -174.42  -5.426357   
13  2025-05-19 12:05:00     1.12631  0  0   {}   402.66  -3.723404   
14  2025-05-29 02:35:00     1.12614  0  0   {}   -95.31  -3.369434   
15  2025-06-23 00:00:00     1.14562  0  0   {}   217.46  -3.093923   
16  2025-07-07 11:50:00     1.17335  0  0   {}  -140.56  -4.099561   
17  2025-07-10 17:25:00     1.16752  0  0   {}  -206.03  -7.035176   
18  2025-08-01 15:30:00      1.1399  0  0   {}   886.09  -2.802803   
19  2025-08-06 16:10:00     1.16282  0  0   {}  -227.62  -4.658902   
20  2025-08-20 21:25:00      1.1658  0  0   {}   115.92  -2.575897   

     profit_net profit_cumulative       balance  
0   -223.862281       -223.862281   9776.137719  
1   -212.116749        -435.97903    9564.02097  
2    -78.861631       -514.840661   9485.159339  
3    -994.76433      -1509.604991   8490.395009  
4     55.458506      -1454.146485   8545.853515  
5   -466.745498      -1920.891984   8079.108016  
6   -151.954153      -2072.846136   7927.153864  
7   -205.996667      -2278.842803   7721.157197  
8   -212.332667       -2491.17547    7508.82453  
9   -219.857059      -2711.032529   7288.967471  
10  -242.441608      -2953.474137   7046.525863  
11  2273.215146        -680.25899    9319.74101  
12  -179.846357       -860.105347   9139.894653  
13 

In [17]:
mm = bt.plot_balance()
display(mm)

In [18]:
pnl_chart = bt.plot_pnl()
display(pnl_chart)

In [19]:
evaluate_backtest(bt.trades)

Daily Drawdown : -1144.53
Max Drawdown (portfolio): -3476.80
worst trades (trade MAE): [np.float64(nan), np.float64(nan), np.float64(-758.0141843971652), np.float64(-1144.530046224902), np.float64(-173.56321839080397), np.float64(-550.9518477043736), np.float64(nan), np.float64(nan), np.float64(nan), np.float64(nan), np.float64(nan), np.float64(-567.4853801169644), np.float64(nan), np.float64(-225.53191489361905), np.float64(-339.35018050542266), np.float64(-150.27624309392937), np.float64(-414.0556368960611), np.float64(nan), np.float64(-674.2742742742618), np.float64(nan), np.float64(-150.1379944802217)]
max_intrabar_drawdown: -1144.53
biggest_profit: 2276.49
equity_daily_drawdown: -990.45
equity_max_drawown: -2729.61
avg_win: 659.35
avg_loss: -254.05
count_profit_trades: 6
count_loss_trades: 15
Win Rate1: 28.57%
rrr: 2.6


order_type  profit
0        buy  287.79
1       sell -142.42

state  symbol order_type        volume           open_time open_price  \
4   closed  EURUSD       sell  28735.632184 2025-02-04 18:45:00    1.03823   
11  closed  EURUSD        buy  46783.625731 2025-03-20 12:20:00    1.08543   
13  closed  EURUSD       sell  53191.489362 2025-05-02 12:35:00    1.13388   
15  closed  EURUSD        buy  44198.895028 2025-06-06 15:30:00     1.1407   
18  closed  EURUSD       sell   40040.04004 2025-07-16 18:15:00    1.16203   
20  closed  EURUSD       sell  36798.528059 2025-08-07 11:00:00    1.16895   

            close_time close_price sl tp  ...   profit  commission  \
4  2025-02-11 21:40:00     1.03623  0  0  ...    57.47   -2.011494   
11 2025-04-23 01:25:00     1.13409  0  0  ...  2276.49   -3.274854   
13 2025-05-19 12:05:00     1.12631  0  0  ...   402.66   -3.723404   
15 2025-06-23 00:00:00     1.14562  0  0  ...   217.46   -3.093923   
18 2025-08-01 15:30:00      1.1399  0  0  ...   886.09   -2.802803   
20 2025-08-20 21:25:00      1.1658  0  0  ...   115.92   -2.575897   

     profit_net profit_cumulative       balance        date  \
4     55.458506      -1454.146485   8545.853515  2025-02-04   
11  2273.215146        -680.25899    9319.74101  2025-03-20   
13   398.936596       -461.168751   9538.831249  2025-05-02   
15   214.366077       -345.482108   9654.517892  2025-06-06   
18   883.287197        180.080352  10180.080352  2025-07-16   
20   113.344103         61.145553  10061.145553  2025-08-07   

                  time intrabar_drawdown  current_max     drawdown  
4  2025-02-11 21:40:00       -173.563218  -223.862281 -1230.284205  
11 2025-04-23 01:25:00       -567.485380  -223.862281   -456.39671  
13 2025-05-19 12:05:00       -225.531915  -223.862281  -237.306471  
15 2025-06-23 00:00:00       -150.276243  -223.862281  -121.619828  
18 2025-08-01 15:30:00       -674.274274   180.080352          0.0  
20 2025-08-20 21:25:00       -150.137994   180.080352  -118.934799  

[6 rows x 21 columns]

state  symbol order_type         volume           open_time open_price  \
0   closed  EURUSD       sell   70175.438596 2025-01-06 09:30:00    1.03191   
1   closed  EURUSD       sell   55096.418733 2025-01-14 00:50:00    1.02647   
2   closed  EURUSD       sell   56737.588652 2025-01-15 15:30:00    1.03007   
3   closed  EURUSD        buy   61633.281972 2025-01-23 18:10:00    1.03964   
5   closed  EURUSD       sell   44792.833147 2025-02-12 19:00:00    1.03914   
6   closed  EURUSD        buy   74487.895717 2025-02-27 06:30:00    1.04657   
7   closed  EURUSD       sell   66666.666667 2025-03-03 03:10:00    1.04202   
8   closed  EURUSD       sell   34752.389227 2025-03-04 13:50:00    1.05266   
9   closed  EURUSD        buy   73529.411765 2025-03-13 10:35:00    1.08682   
10  closed  EURUSD        buy   64308.681672 2025-03-19 10:35:00    1.09024   
12  closed  EURUSD        buy   77519.379845 2025-04-30 04:55:00    1.13684   
14  closed  EURUSD        buy   48134.777377 2025-05-22 18:05:00    1.12812   
16  closed  EURUSD        buy   58565.153734 2025-07-02 14:35:00    1.17575   
17  closed  EURUSD        buy  100502.512563 2025-07-10 16:50:00    1.16957   
19  closed  EURUSD       sell   66555.740433 2025-08-06 13:10:00     1.1594   

            close_time close_price sl tp  ...  profit  commission  profit_net  \
0  2025-01-06 11:00:00     1.03503  0  0  ... -218.95   -4.912281 -223.862281   
1  2025-01-14 21:35:00     1.03025  0  0  ... -208.26   -3.856749 -212.116749   
2  2025-01-20 15:30:00     1.03139  0  0  ...  -74.89   -3.971631  -78.861631   
3  2025-02-03 00:00:00     1.02357  0  0  ... -990.45    -4.31433  -994.76433   
5  2025-02-20 20:15:00     1.04949  0  0  ... -463.61   -3.135498 -466.745498   
6  2025-02-27 15:50:00      1.0446  0  0  ... -146.74   -5.214153 -151.954153   
7  2025-03-03 13:30:00     1.04504  0  0  ... -201.33   -4.666667 -205.996667   
8  2025-03-04 20:55:00      1.0587  0  0  ... -209.90   -2.432667 -212.332667   
9  2025-03-13 15:45:00      1.0839  0  0  ... -214.71   -5.147059 -219.857059   
10 2025-03-19 20:35:00     1.08654  0  0  ... -237.94   -4.501608 -242.441608   
12 2025-04-30 18:25:00     1.13459  0  0  ... -174.42   -5.426357 -179.846357   
14 2025-05-29 02:35:00     1.12614  0  0  ...  -95.31   -3.369434  -98.679434   
16 2025-07-07 11:50:00     1.17335  0  0  ... -140.56   -4.099561 -144.659561   
17 2025-07-10 17:25:00     1.16752  0  0  ... -206.03   -7.035176 -213.065176   
19 2025-08-06 16:10:00     1.16282  0  0  ... -227.62   -4.658902 -232.278902   

   profit_cumulative      balance        date                time  \
0        -223.862281  9776.137719  2025-01-06 2025-01-06 11:00:00   
1         -435.97903   9564.02097  2025-01-14 2025-01-14 21:35:00   
2        -514.840661  9485.159339  2025-01-15 2025-01-20 15:30:00   
3       -1509.604991  8490.395009  2025-01-23 2025-02-03 00:00:00   
5       -1920.891984  8079.108016  2025-02-12 2025-02-20 20:15:00   
6       -2072.846136  7927.153864  2025-02-27 2025-02-27 15:50:00   
7       -2278.842803  7721.157197  2025-03-03 2025-03-03 13:30:00   
8        -2491.17547   7508.82453  2025-03-04 2025-03-04 20:55:00   
9       -2711.032529  7288.967471  2025-03-13 2025-03-13 15:45:00   
10      -2953.474137  7046.525863  2025-03-19 2025-03-19 20:35:00   
12       -860.105347  9139.894653  2025-04-30 2025-04-30 18:25:00   
14       -559.848186  9440.151814  2025-05-22 2025-05-29 02:35:00   
16       -490.141669  9509.858331  2025-07-02 2025-07-07 11:50:00   
17       -703.206845  9296.793155  2025-07-10 2025-07-10 17:25:00   
19         -52.19855   9947.80145  2025-08-06 2025-08-06 16:10:00   

   intrabar_drawdown  current_max     drawdown  
0                NaN  -223.862281          0.0  
1                NaN  -223.862281  -212.116749  
2        -758.014184  -223.862281  -290.978381  
3       -1144.530046  -223.862281  -1285.74271  
5        -550.951848  -223.862281 -1697.029703  
6                NaN  -223.862281 -1848.9838

state  symbol order_type         volume           open_time open_price  \
0   closed  EURUSD       sell   70175.438596 2025-01-06 09:30:00    1.03191   
1   closed  EURUSD       sell   55096.418733 2025-01-14 00:50:00    1.02647   
2   closed  EURUSD       sell   56737.588652 2025-01-15 15:30:00    1.03007   
3   closed  EURUSD        buy   61633.281972 2025-01-23 18:10:00    1.03964   
4   closed  EURUSD       sell   28735.632184 2025-02-04 18:45:00    1.03823   
5   closed  EURUSD       sell   44792.833147 2025-02-12 19:00:00    1.03914   
6   closed  EURUSD        buy   74487.895717 2025-02-27 06:30:00    1.04657   
7   closed  EURUSD       sell   66666.666667 2025-03-03 03:10:00    1.04202   
8   closed  EURUSD       sell   34752.389227 2025-03-04 13:50:00    1.05266   
9   closed  EURUSD        buy   73529.411765 2025-03-13 10:35:00    1.08682   
10  closed  EURUSD        buy   64308.681672 2025-03-19 10:35:00    1.09024   
11  closed  EURUSD        buy   46783.625731 2025-03-20 12:20:00    1.08543   
12  closed  EURUSD        buy   77519.379845 2025-04-30 04:55:00    1.13684   
13  closed  EURUSD       sell   53191.489362 2025-05-02 12:35:00    1.13388   
14  closed  EURUSD        buy   48134.777377 2025-05-22 18:05:00    1.12812   
15  closed  EURUSD        buy   44198.895028 2025-06-06 15:30:00     1.1407   
16  closed  EURUSD        buy   58565.153734 2025-07-02 14:35:00    1.17575   
17  closed  EURUSD        buy  100502.512563 2025-07-10 16:50:00    1.16957   
18  closed  EURUSD       sell    40040.04004 2025-07-16 18:15:00    1.16203   
19  closed  EURUSD       sell   66555.740433 2025-08-06 13:10:00     1.1594   
20  closed  EURUSD       sell   36798.528059 2025-08-07 11:00:00    1.16895   

            close_time close_price sl tp  ...       balance        date  \
0  2025-01-06 11:00:00     1.03503  0  0  ...   9776.137719  2025-01-06   
1  2025-01-14 21:35:00     1.03025  0  0  ...    9564.02097  2025-01-14   
2  2025-01-20 15:30:00     1.03139  0  0  ...   9485.159339  2025-01-15   
3  2025-02-03 00:00:00     1.02357  0  0  ...   8490.395009  2025-01-23   
4  2025-02-11 21:40:00     1.03623  0  0  ...   8545.853515  2025-02-04   
5  2025-02-20 20:15:00     1.04949  0  0  ...   8079.108016  2025-02-12   
6  2025-02-27 15:50:00      1.0446  0  0  ...   7927.153864  2025-02-27   
7  2025-03-03 13:30:00     1.04504  0  0  ...   7721.157197  2025-03-03   
8  2025-03-04 20:55:00      1.0587  0  0  ...    7508.82453  2025-03-04   
9  2025-03-13 15:45:00      1.0839  0  0  ...   7288.967471  2025-03-13   
10 2025-03-19 20:35:00     1.08654  0  0  ...   7046.525863  2025-03-19   
11 2025-04-23 01:25:00     1.13409  0  0  ...    9319.74101  2025-03-20   
12 2025-04-30 18:25:00     1.13459  0  0  ...   9139.894653  2025-04-30   
13 2025-05-19 12:05:00     1.12631  0  0  ...   9538.831249  2025-05-02   
14 2025-05-29 02:35:00     1.12614  0  0  ...   9440.151814  2025-05-22   
15 2025-06-23 00:00:00     1.14562  0  0  ...   9654.517892  2025-06-06   
16 2025-07-07 11:50:00     1.17335  0  0  ...   9509.858331  2025-07-02   
17 2025-07-10 17:25:00     1.16752  0  0  ...   9296.793155  2025-07-10   
18 2025-08-01 15:30:00      1.1399  0  0  ...  10180.080352  2025-07-16   
19 2025-08-06 16:10:00     1.16282  0  0  ...    9947.80145  2025-08-06   
20 2025-08-20 21:25:00      1.1658  0  0  ...  10061.145553  2025-08-07   

                  time intrabar_drawdown current_max     drawdown dayofweek  \
0  2025-01-06 11:00:00               NaN -223.862281          0.0         0   
1  2025-01-14 21:35:00               NaN -223.862281  -212.116749         1   
2  2025-01-20 15:30:00       -758.014184 -223.862281  -290.978381         2   
3  2025-02-03 00:00:00      -1144.530046 -223.862281  -1285.74271         3   
4  2025-02-11 21:40:00       -173.563218 -223.862281 -1230.284205         1   
5  2025-02-20 20:15:00       -550.951848 -223.862281 -1697.029703         2   
6  2025-02-27 15:50:00               NaN -223.862281 -1848.983

max_drawdown -2729.61


In [20]:
# visualizing the ohlc data
fig = go.Figure(data = [go.Candlestick(x = ohlc_df['time'],
                                        open = ohlc_df['open'],
                                        high = ohlc_df['high'],
                                        low = ohlc_df['low'],
                                        close = ohlc_df['close'])])

# fig.update_layout(height=600, xaxis_rangeslider_visible=False)
# 📌 Add Pivot Points as Horizontal Lines
pivot_levels = ["sell_stope_loss", "R2", "buy_stope_loss", "S2"]
colors = {'sell_stope_loss': 'red', 'buy_stope_loss': 'red', 'R2': 'green', 'S2': 'green'}


for _, row in daily_df.iterrows():
    for level in pivot_levels:
        fig.add_trace(go.Scatter(
            x=[row['time'], row['time'] + pd.Timedelta(days=1)],  # Extend for one day
            y=[row[level], row[level]],
            mode='lines',
            name=f"{level} {row['time']}",
            line=dict(color=colors[level], width=1.5, dash='dot')
        ))

# 📌 Customize Layout
fig.update_layout(
    title="Pivot Points on Candlestick Chart",
    xaxis_title="Date",
    yaxis_title="Price",
    template="plotly_dark",
    xaxis_rangeslider_visible=False
)
fig